# VR EyeTracking Data Analysis
IGMS 789
Chengyi Ma


In [2]:
# First import necessary modules
import pandas
import numpy
import plotly
import os
from Event_Detector.Library.DataPlotter import DataPlotter

# Second read the vr data
file_path = "E:/Eye Tracking Recordings/02-23-2022-VR/2022-02-23-11-25.txt"
dataFrame = pandas.read_csv(file_path, delimiter='\t')

print(dataFrame.columns)


Index(['frameNumber', 'unityTimeAtLog', 'cameraPos_x', 'cameraPos_y',
       'cameraPos_z', 'cameraMat_R0C0', 'cameraMat_R0C1', 'cameraMat_R0C2',
       'cameraMat_R0C3', 'cameraMat_R1C0', 'cameraMat_R1C1', 'cameraMat_R1C2',
       'cameraMat_R1C3', 'cameraMat_R2C0', 'cameraMat_R2C1', 'cameraMat_R2C2',
       'cameraMat_R2C3', 'cameraMat_R3C0', 'cameraMat_R3C1', 'cameraMat_R3C2',
       'cameraMat_R3C3', 'yTargetPos_x', 'yTargetPos_y', 'yTargetPos_z',
       'rTargetPos_x', 'rTargetPos_y', 'rTargetPos_z', 'bTargetPos_x',
       'bTargetPos_y', 'bTargetPos_z', 'wTargetPos_x', 'wTargetPos_y',
       'wTargetPos_z', 'confidence', 'gaze_timestamp',
       'unityTimeAtEyeImageCapture', 'gaze_normal2_x', 'gaze_normal2_y',
       'gaze_normal2_z', 'gaze_normal0_x', 'gaze_normal0_y', 'gaze_normal0_z',
       'gaze_normal1_x', 'gaze_normal1_y', 'gaze_normal1_z', 'gaze_point_3d_x',
       'gaze_point_3d_y', 'gaze_point_3d_z', 'eye_center0_3d_x',
       'eye_center0_3d_y', 'eye_center0_3d_z', 'ey

## Assignment Question 01: 
**What was Pupil Lab’s sampling rate?**<br>
To find the sampling rate is to calculate the number of data samples per second. That equals to total samples divided by total times. The sample rate variation is assumed to be small and neglectable.<br>
In order to get the time data, we need to look at timestamp columns and there are three of them.

In [3]:
print(dataFrame[["unityTimeAtLog","gaze_timestamp","unityTimeAtEyeImageCapture"]])

      unityTimeAtLog  gaze_timestamp  unityTimeAtEyeImageCapture
0           79.96877  -752923.714251                   79.873064
1           79.96893  -752923.710257                   79.877059
2           79.96896  -752923.704240                   79.883075
3           79.96900  -752923.700238                   79.887077
4           79.96904  -752923.696254                   79.891061
...              ...             ...                         ...
4752        99.93494  -752903.730261                   99.857054
4753        99.93498  -752903.726295                   99.861020
4754        99.93501  -752903.722291                   99.865024
4755        99.93505  -752903.718266                   99.869049
4756        99.93509  -752903.714270                   99.873045

[4757 rows x 3 columns]


Since that the data involves unity object's location and position. *unityTimeAtEyeImageCapture* should be used for best synchronization.
The total time recorded by *unityTimeAtEyeImageCapture* is:

In [4]:
totalUnitySamples = dataFrame.shape[0]
time_start	= dataFrame["unityTimeAtEyeImageCapture"][0]
time_end	= dataFrame["unityTimeAtEyeImageCapture"][totalUnitySamples-1]
timestampNPY = numpy.load("E:/Eye Tracking Recordings/02-23-2022-VR/000/eye0_timestamps.npy")
print("Total samples from pupil lab: ", timestampNPY.size) # data from pupil lab files, not from this data
print("Total samples from unity: ", dataFrame.shape[0])
timeDuration = time_end - time_start
print("Time duration of data: ", timeDuration)
print("Sample rate: ", totalUnitySamples / timeDuration)

Total samples from pupil lab:  12066
Total samples from unity:  4757
Time duration of data:  19.99998099997171
Sample rate:  237.85022595805108


So the binocular gaze data has a sampling rate of **237.8** (240 if frame drops are considered).

## Assignment Question 02:
**Was the sampling rate consistent over the duration of the recording?**<br>
To find if the time is consistent, we need to know the frame rate of each second.

In [5]:
rate_array = numpy.zeros(20)
for i in range(1, 21):
	currentSecondSamples_ceiled = dataFrame.loc[ (dataFrame["unityTimeAtEyeImageCapture"] <= time_start+i)]
	currentSecondSamples = currentSecondSamples_ceiled.loc[currentSecondSamples_ceiled["unityTimeAtEyeImageCapture"] >= time_start+i-1]
	rate_array[i-1] = currentSecondSamples.shape[0]
print(rate_array)
print("Standard Deviation: ", numpy.std(rate_array))

[240. 240. 240. 241. 240. 240. 240. 240. 240. 240. 240. 240. 240. 240.
 240. 196. 240. 240. 240. 240.]
Standard Deviation:  9.603514981505468


It seems that the frame rate is consistent.

## Assignment Question 02
**What does the data look like in spherical coordinates (azimuth/elevation)?**
Using the previously developed data processing method, generate a spherical coordinate graph.

In [21]:

def calculateSphericalCoordinate(row: pandas.Series, varName: str) -> tuple:
	x = row['{}_x'.format(varName)]
	y = row['{}_y'.format(varName)]
	z = row['{}_z'.format(varName)]

	azimuth = numpy.rad2deg(numpy.arctan(numpy.divide(x,z)))
	elevation = numpy.rad2deg(numpy.arctan(numpy.divide(y,z)))

	return (azimuth, elevation)

sphericalCoordinates = dataFrame.apply(lambda rowInterator: calculateSphericalCoordinate(row=rowInterator, varName="gaze_point_3d"), axis=1)
dataFrame["normalTimeStamp"] = dataFrame['unityTimeAtEyeImageCapture'] - dataFrame['unityTimeAtEyeImageCapture'].iloc[0]
dataFrame['gaze_az'],dataFrame['gaze_el'] = zip(*sphericalCoordinates)

plotter = DataPlotter(['gaze_az', 'gaze_el'], dataFrame)
plotter.plot_layout["xaxis"]["range"] = [0, 20]
plotter.plot(timeColumnName = "normalTimeStamp")

## Assignment Question 04:
**How does the tracker noise during fixation compare to data collected using the mobile eye tracker?**<br>
Redraw a graph from previous data collected with mobile eye tracker

In [22]:
from Event_Detector.Library.EventDetector import EventDetector
from Event_Detector.Library.DataManager import DataManager
from Event_Detector.Library.DataPlotter import DataPlotter

data_path = "E:/Eye Tracking Recordings/2022_01_28/004/exports/000"
dispersion_threshold =  2#
data_manager = DataManager(data_path)
data_manager.initilizeData()

ed = EventDetector(data_manager.gaze_data)
ed.process_data()
plotter2 = DataPlotter(["gaze_az", "gaze_el"], ed.gaze_data)
plotter2.plot_layout["xaxis"]["range"] = [0, 20]
plotter2.plot()


Creating DataManager
DataManager created.
Initializing Data...
Done.


The two graphs both have a range of [0, 20] seconds by default. By comparing the two default graphs, it is easy to notice that the VR data set has a higher level of noise than the post-hoc processed data collected by the mobile devices. But, interestingly, the VR data does not display a clear blink event. 

## Assignment Question 05:<br> 
**Can the tracker noise be reduced through the application of a filter?**<br>
First, apply window average filter:

In [19]:
from Event_Detector.Library.DataFilter import DataFilter

window_size = 50

dataFilter = DataFilter(dataFrame)
dataFilter.applyWindowAverage(window_size, "gaze_az")
dataFilter.applyWindowAverage(window_size, "gaze_el")

plotter = DataPlotter(["gaze_az", "gaze_el",'gaze_az_WAfilter', 'gaze_el_WAfilter'], dataFrame)
plotter.plot_layout["xaxis"]["range"] = [0, 20]
plotter.plot(timeColumnName = "normalTimeStamp")

To have a clear vision of the effect of the filter, the window is set to 50. It is easy to notice that the noise of sudden changes could be eliminated with a window of 20. However the overall variation caused by the noise is not greatly improved, and the filter also causes a noticable signal delay. <br>
Now, try median filter:

In [20]:
dataFilter.applyMedianFilter(window_size, "gaze_az")
dataFilter.applyMedianFilter(window_size, "gaze_el")

plotter = DataPlotter(["gaze_az", "gaze_el",'gaze_az_MedianFilter', 'gaze_el_MedianFilter'], dataFrame)
plotter.plot_layout["xaxis"]["range"] = [0, 20]
plotter.plot(timeColumnName = "normalTimeStamp")

Median filtering is less effective than the window average filter in the aspect of denoising. However, it does not cause the signal delay in the data.